<a href="https://colab.research.google.com/github/sclaudiobr/covid2019/blob/master/COVID19_Heatmap.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install --upgrade folium

     |████████████████████████████████| 102kB 3.8MB/s 
ERROR: datascience 0.10.6 has requirement folium==0.2.1, but you'll have folium 0.11.0 which is incompatible.
  Found existing installation: folium 0.8.3
    Uninstalling folium-0.8.3:
      Successfully uninstalled folium-0.8.3


In [2]:
import pandas as pd
import numpy as np
import folium
from folium import plugins
import json
print("Nova versão do Folium: ", folium.__version__)

Nova versão do Folium:  0.11.0


In [3]:
# Aqui, configuramos o acesso ao reposiório e exportação para o formato pandas Dataframe (tabela)
# Observe que aqui usei o terminal LINUX do COLAB para a importacao e descompactação do arquivo.
!wget https://data.brasil.io/dataset/covid19/caso.csv.gz
df = pd.read_csv("caso.csv.gz", compression='gzip')
df.head(10)

--2020-09-29 13:49:23--  https://data.brasil.io/dataset/covid19/caso.csv.gz
Resolving data.brasil.io (data.brasil.io)... 104.26.9.175, 104.26.8.175, 172.67.71.45, ...
Connecting to data.brasil.io (data.brasil.io)|104.26.9.175|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 7982758 (7.6M) [application/gzip]
Saving to: ‘caso.csv.gz’

caso.csv.gz         100%[===================>]   7.61M  7.31MB/s    in 1.0s    

2020-09-29 13:49:24 (7.31 MB/s) - ‘caso.csv.gz’ saved [7982758/7982758]



date state  ... confirmed_per_100k_inhabitants death_rate
0  2020-09-28    AC  ...                     3161.79764     0.0236
1  2020-09-27    AC  ...                     3160.55038     0.0236
2  2020-09-26    AC  ...                     3158.84958     0.0235
3  2020-09-25    AC  ...                     3141.95491     0.0236
4  2020-09-24    AC  ...                     3124.49330     0.0237
5  2020-09-23    AC  ...                     3106.46476     0.0238
6  2020-09-22    AC  ...                     3089.34332     0.0239
7  2020-09-21    AC  ...                     3073.46913     0.0239
8  2020-09-20    AC  ...                     3070.40768     0.0240
9  2020-09-19    AC  ...                     3068.36672     0.0239

[10 rows x 12 columns]

In [4]:
# Aqui, configuramos o acesso ao reposiório e exportação para o formato pandas Dataframe (tabela)
# Observe que aqui usei o terminal LINUX do COLAB para a importacao e descompactação do arquivo.
!wget https://data.brasil.io/dataset/covid19/caso.csv.gz
!gunzip caso.csv.gz
df = pd.read_csv("caso.csv")
df.head(10)

--2020-09-29 13:49:30--  https://data.brasil.io/dataset/covid19/caso.csv.gz
Resolving data.brasil.io (data.brasil.io)... 104.26.9.175, 104.26.8.175, 172.67.71.45, ...
Connecting to data.brasil.io (data.brasil.io)|104.26.9.175|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 7982758 (7.6M) [application/gzip]
Saving to: ‘caso.csv.gz.1’

caso.csv.gz.1       100%[===================>]   7.61M  7.24MB/s    in 1.1s    

2020-09-29 13:49:31 (7.24 MB/s) - ‘caso.csv.gz.1’ saved [7982758/7982758]



date state  ... confirmed_per_100k_inhabitants death_rate
0  2020-09-28    AC  ...                     3161.79764     0.0236
1  2020-09-27    AC  ...                     3160.55038     0.0236
2  2020-09-26    AC  ...                     3158.84958     0.0235
3  2020-09-25    AC  ...                     3141.95491     0.0236
4  2020-09-24    AC  ...                     3124.49330     0.0237
5  2020-09-23    AC  ...                     3106.46476     0.0238
6  2020-09-22    AC  ...                     3089.34332     0.0239
7  2020-09-21    AC  ...                     3073.46913     0.0239
8  2020-09-20    AC  ...                     3070.40768     0.0240
9  2020-09-19    AC  ...                     3068.36672     0.0239

[10 rows x 12 columns]

In [5]:
# Importa dados de localização ponto(lat,long)) das cidades segundo a base de dados do IBGE de 2010
cidades = pd.read_csv('https://raw.githubusercontent.com/sandeco/CanalSandeco/master/covid-19/cidades_brasil.csv')
cidades.head()

codigo_ibge                 nome  latitude  longitude  capital  codigo_uf
0      5200050      Abadia de Goiás -16.75730   -49.4412        0         52
1      3100104  Abadia dos Dourados -18.48310   -47.3916        0         31
2      5200100            Abadiânia -16.19700   -48.7057        0         52
3      3100203               Abaeté -19.15510   -45.4444        0         31
4      1500107           Abaetetuba  -1.72183   -48.8788        0         15

In [6]:
# Aqui fazemos a troca de índice de cidades pelo códifo do IBGE
cidades = cidades.set_index('codigo_ibge')

In [7]:
cidades.head()

nome  latitude  longitude  capital  codigo_uf
codigo_ibge                                                              
5200050          Abadia de Goiás -16.75730   -49.4412        0         52
3100104      Abadia dos Dourados -18.48310   -47.3916        0         31
5200100                Abadiânia -16.19700   -48.7057        0         52
3100203                   Abaeté -19.15510   -45.4444        0         31
1500107               Abaetetuba  -1.72183   -48.8788        0         15

In [8]:
cities = df.loc[df.place_type == 'city',:]
cities.place_type.unique()

array(['city'], dtype=object)

In [9]:
# juntar as duas bases de dados (IBGE cidades) come guardar na variável cities
cities = cities.join(cidades, on='city_ibge_code')

In [10]:
# selecionar as colunas de interesse da tabela "cities", 
# geo_last são os ultimos registros da tabela para cada cidade
geo_last = cities.loc[cities.is_last==True,['city','latitude', 'longitude','state','confirmed','deaths']]
geo_last.head()

city  latitude  longitude state  confirmed  deaths
196    Acrelândia  -9.82581   -66.8972    AC        468       9
372  Assis Brasil -10.92980   -69.5738    AC        617       9
515     Brasiléia -10.99500   -68.7497    AC       1165      20
650        Bujari  -9.81528   -67.9550    AC        374       7
816      Capixaba -10.56600   -67.6860    AC        250       7

In [11]:
#Quantidade de cidades com casos de covid-19
len(geo_last)

5580

In [12]:
#Quantidade de casos confirmados 
geo_last.confirmed.sum()

4665667

In [13]:
#Quantidade de mortes por covid-19
geo_last.deaths.sum()

140332

In [14]:
#Porcentagem de mortos sobre os casos confirmados
geo_last.deaths.sum()/geo_last.confirmed.sum()*100

3.0077585905723665

In [15]:
# verificar se todos os estados estão inseridos
len(geo_last.state.unique())

27

In [16]:
# Separando o conjunto de dados da interpolação
coordenadas = geo_last[['latitude','longitude','confirmed']]
#retirar as linhas que tiver dados faltando
coordenadas = coordenadas.dropna()
coordenadas.head()

latitude  longitude  confirmed
196  -9.82581   -66.8972        468
372 -10.92980   -69.5738        617
515 -10.99500   -68.7497       1165
650  -9.81528   -67.9550        374
816 -10.56600   -67.6860        250

In [17]:
baseMap = folium.Map(
    width = '100%',   height = '100%',
    location = [-15.77972, -47.92972], # <- Brasil
    zoom_start = 4
)

In [18]:
baseMap

In [19]:
baseMap = baseMap.add_child(plugins.HeatMap(coordenadas))

In [20]:
baseMap

In [21]:
# retirar dados faltantes
geo_last = geo_last.dropna()
geo_last.head(5)

city  latitude  longitude state  confirmed  deaths
196    Acrelândia  -9.82581   -66.8972    AC        468       9
372  Assis Brasil -10.92980   -69.5738    AC        617       9
515     Brasiléia -10.99500   -68.7497    AC       1165      20
650        Bujari  -9.81528   -67.9550    AC        374       7
816      Capixaba -10.56600   -67.6860    AC        250       7

In [22]:
for i in range(0,len(geo_last)):
    folium.Circle(
        location = [geo_last.iloc[i]['latitude'], geo_last.iloc[i]['longitude']],
        color = '#00FF69',
        fill = '#00A1B3',
        tooltip = '<li><bold> CIDADE: '+ str(geo_last.iloc[i]['city']) + "</li></bold>" +
                 '<li><bold> ESTADO: '+ str(geo_last.iloc[i]['state']) +"</li></bold>" +
                 '<li><bold> CONFIRMADOS: '+ str(geo_last.iloc[i]['confirmed'])+"</li></bold>" +
                 '<li><bold> MORTES: '+ str(geo_last.iloc[i]['deaths']) + "</li></bold>" ,
        radius = (geo_last.iloc[i]['confirmed']**0.78)
                                            
    ).add_to(baseMap)
#baseMap

In [23]:
# importando logomarca e colocando no mapa
from folium.plugins import FloatImage
url = 'https://raw.githubusercontent.com/sclaudiobr/algoritmos-py/master/text43.png'
FloatImage(url,bottom=10,left=55).add_to(baseMap)
baseMap

In [24]:
baseMap.save('heatmap-cidade.html')